In [ ]:
from google.colab import drive
drive.mount('/content/drive')
!unzip "/content/drive/MyDrive/AI Year 3/Challenges/Week 2 and 3/com3025-2022-image-classification-challenge.zip" -d "/content/drive/MyDrive/AI Year 3/Challenges/Week 2 and 3/"

Streaming output truncated to the last 5000 lines.
  inflating: /content/drive/MyDrive/AI Year 3/Challenges/Week 2 and 3/test/84ae209d-774a-42fd-a6ca-314d13b2b26f.jpg  
  inflating: /content/drive/MyDrive/AI Year 3/Challenges/Week 2 and 3/test/84b39e86-d3ee-4667-9c46-759889c13074.jpg  
  inflating: /content/drive/MyDrive/AI Year 3/Challenges/Week 2 and 3/test/84b6e58a-299d-4933-96ec-425de705bca4.jpg  
  inflating: /content/drive/MyDrive/AI Year 3/Challenges/Week 2 and 3/test/84be64bd-09b3-4c65-acbe-7a1b4fce5219.jpg  
  inflating: /content/drive/MyDrive/AI Year 3/Challenges/Week 2 and 3/test/84c3a893-c687-45cc-9025-90e3eb1e5fd0.jpg  
  inflating: /content/drive/MyDrive/AI Year 3/Challenges/Week 2 and 3/test/84cb549c-ad48-496e-9bcd-443a0967284e.jpg  
  inflating: /content/drive/MyDrive/AI Year 3/Challenges/Week 2 and 3/test/84ccc098-8b2b-4448-9304-6626a9cdfd30.jpg  
  inflating: /content/drive/MyDrive/AI Year 3/Challenges/Week 2 and 3/test/84d88fe1-f9fc-4aa9-b2f8-baebd7d8c629.jpg  
  inf

In [ ]:
import numpy as np 
import pandas as pd 
import os
from tqdm import tqdm
import csv
import cv2
import matplotlib.pyplot as plt
from keras.preprocessing.image import ImageDataGenerator
from tensorflow.keras.applications import ResNet50
from tensorflow.keras import optimizers
from keras.layers import Dense
from keras.layers import Dropout
from keras.models import Sequential
from tensorflow.keras.utils import to_categorical
from sklearn.model_selection import train_test_split
import re
from google.colab import files

In [ ]:
# resize image to feed into model
def read_and_resize_image(image_path):  
    im = cv2.imread(image_path)
    print(im)
    im_resized = cv2.resize(im, (224, 224), interpolation=cv2.INTER_LINEAR)
    im_converted = cv2.cvtColor(im_resized, cv2.COLOR_BGR2RGB)
    return im_converted
import matplotlib.pyplot as plt
    
# plot image function to check predictions
def show_picture(im_rgb):
    plt.imshow(im_rgb)
    plt.show()
    
# alter image to make the model easier to read
imgGen = ImageDataGenerator(
    shear_range = 0.25,
    zoom_range = 0.25,
)


In [ ]:
train_location = "/content/drive/MyDrive/AI Year 3/Challenges/Week 2 and 3/train.csv"
file_location = "/content/drive/MyDrive/AI Year 3/Challenges/Week 2 and 3/"
train_dataset = pd.read_csv(train_location)


# get all the images in an array
images = train_dataset['file_path'].values.astype(str)
i = 0
imagesnew = []
while i < len(images):
    imagesnew.append(file_location+images[i])
    i+= 1
    
# get labels
labels = train_dataset['label'].values

file_ids = []
i = 0
while i < len(images):
    file_ids.append([imagesnew[i], labels[i].astype(str)])
    i+=1

y = []

image_data = []

i = 0
while i < len(images):
  image_data.append(read_and_resize_image(file_ids[i][0]))
  y.append(file_ids[i][1])
  i += 1    

Streaming output truncated to the last 5000 lines.
  [ 48  96  60]
  [ 44  91  58]]]
[[[ 33 106  80]
  [ 33 106  80]
  [ 33 106  80]
  ...
  [ 82 173 118]
  [ 82 173 118]
  [ 82 173 118]]

 [[ 32 105  79]
  [ 32 105  79]
  [ 32 105  79]
  ...
  [ 81 172 117]
  [ 81 172 117]
  [ 81 172 117]]

 [[ 31 102  76]
  [ 31 102  76]
  [ 29 102  76]
  ...
  [ 81 172 117]
  [ 81 172 117]
  [ 81 172 117]]

 ...

 [[114 174 120]
  [113 173 119]
  [112 172 118]
  ...
  [ 27  79  56]
  [ 27  79  56]
  [ 27  79  56]]

 [[114 174 120]
  [113 173 119]
  [112 172 118]
  ...
  [ 23  75  52]
  [ 23  75  52]
  [ 23  75  52]]

 [[114 174 120]
  [113 173 119]
  [112 172 118]
  ...
  [ 20  72  49]
  [ 20  72  49]
  [ 20  72  49]]]
[[[132 143 103]
  [133 144 104]
  [133 144 104]
  ...
  [255 109 223]
  [252 110 223]
  [251 112 223]]

 [[130 141 101]
  [131 142 102]
  [131 142 102]
  ...
  [255 108 223]
  [253 109 222]
  [250 110 223]]

 [[128 139  99]
  [128 139  99]
  [129 140 100]
  ...
  [255 106 224]
  [252 

In [ ]:
y = to_categorical(y)
X = image_data

X = np.asarray(X)

X_train, X_valid, y_train, y_valid = train_test_split(X, y, random_state = 42, test_size = 0.2)

In [ ]:
epochs = 20
batch_size = 30
def create_model():

    model = Sequential()
    
    model.add(ResNet50(include_top = False, pooling = 'avg', weights = 'imagenet', classes=102))
    model.add(Dropout(0.5))
    model.add(Dense(102, activation="softmax"))
    
    

    return model


model = create_model()#adam  rmsprop  categorical     
model.compile(optimizer= optimizers.Adam(learning_rate = 0.0005, clipnorm = 1.), loss='categorical_crossentropy', metrics=['categorical_accuracy'])

94781440/94765736 [==============================] - 0s 0us/step


In [ ]:
history = model.fit(X_train, y_train, validation_data=(X_valid,y_valid), epochs= epochs, batch_size = batch_size)

Epoch 1/20
55/55 [==============================] - 41s 350ms/step - loss: 3.4576 - categorical_accuracy: 0.2616 - val_loss: 15.8407 - val_categorical_accuracy: 0.0784
Epoch 2/20
55/55 [==============================] - 17s 304ms/step - loss: 1.2364 - categorical_accuracy: 0.6826 - val_loss: 8.5513 - val_categorical_accuracy: 0.1495
Epoch 3/20
55/55 [==============================] - 17s 306ms/step - loss: 0.5919 - categorical_accuracy: 0.8407 - val_loss: 2.8622 - val_categorical_accuracy: 0.4412
Epoch 4/20
55/55 [==============================] - 17s 308ms/step - loss: 0.3562 - categorical_accuracy: 0.9038 - val_loss: 2.4428 - val_categorical_accuracy: 0.5221
Epoch 5/20
55/55 [==============================] - 17s 309ms/step - loss: 0.2307 - categorical_accuracy: 0.9418 - val_loss: 2.8481 - val_categorical_accuracy: 0.4681
Epoch 6/20
55/55 [==============================] - 17s 313ms/step - loss: 0.2149 - categorical_accuracy: 0.9418 - val_loss: 3.2266 - val_categorical_accuracy: 0.44

In [ ]:
#import os
X_test = []
test_location = '/content/drive/MyDrive/AI Year 3/Challenges/Week 2 and 3/test/'

test_files = [(test_location+x) for (x) in os.listdir(test_location)]


for test_image_path in tqdm(test_files):
  X_test.append(read_and_resize_image(test_image_path))


X_test = np.asarray(X_test)

  0%|          | 0/6149 [00:00<?, ?it/s]

[[[37 22 30]
  [35 20 28]
  [33 18 26]
  ...
  [43 43 43]
  [42 42 42]
  [41 41 41]]

 [[36 21 29]
  [35 20 28]
  [34 19 27]
  ...
  [39 39 39]
  [39 39 39]
  [38 38 38]]

 [[34 19 27]
  [34 19 27]
  [35 20 28]
  ...
  [36 36 36]
  [36 36 36]
  [35 35 35]]

 ...

 [[ 8  1  4]
  [ 7  0  3]
  [ 7  0  3]
  ...
  [ 2 33 30]
  [ 2 33 30]
  [ 3 34 31]]

 [[ 8  1  4]
  [ 7  0  3]
  [ 7  0  3]
  ...
  [ 2 33 30]
  [ 2 33 30]
  [ 3 34 31]]

 [[ 8  1  4]
  [ 7  0  3]
  [ 7  0  3]
  ...
  [ 2 33 30]
  [ 2 33 30]
  [ 3 34 31]]]
[[[22 73 45]
  [22 73 45]
  [22 73 45]
  ...
  [10 31 23]
  [11 32 24]
  [12 33 25]]

 [[22 73 45]
  [22 73 45]
  [21 72 44]
  ...
  [10 31 23]
  [11 32 24]
  [11 32 24]]

 [[21 72 44]
  [21 72 44]
  [20 71 43]
  ...
  [ 9 30 22]
  [10 31 23]
  [11 32 24]]

 ...

 [[ 4 13 10]
  [ 4 13 10]
  [ 4 13 10]
  ...
  [12 79 52]
  [11 78 51]
  [10 77 50]]

 [[ 4 13 10]
  [ 4 13 10]
  [ 4 13 10]
  ...
  [11 78 51]
  [10 77 50]
  [10 77 50]]

 [[ 4 13 10]
  [ 4 13 10]
  [ 4 13 10]
  .

  0%|          | 6/6149 [00:00<02:05, 48.87it/s]

[[[ 25  58  44]
  [ 23  56  42]
  [ 23  50  41]
  ...
  [ 11  81  44]
  [ 10  80  43]
  [  8  80  44]]

 [[ 25  58  44]
  [ 23  56  42]
  [ 21  51  40]
  ...
  [ 10  80  43]
  [  8  78  41]
  [  3  75  39]]

 [[ 22  58  42]
  [ 20  55  41]
  [ 19  51  40]
  ...
  [ 12  82  46]
  [  7  77  41]
  [  0  72  36]]

 ...

 [[ 58 133 101]
  [ 58 133 101]
  [ 63 133 102]
  ...
  [ 21  22  43]
  [ 21  22  43]
  [ 21  22  42]]

 [[ 59 134 102]
  [ 60 135 103]
  [ 65 135 104]
  ...
  [ 20  21  42]
  [ 20  21  42]
  [ 20  21  41]]

 [[ 61 136 104]
  [ 61 136 104]
  [ 66 136 105]
  ...
  [ 18  19  40]
  [ 18  19  40]
  [ 18  19  39]]]
[[[ 24  70  51]
  [ 28  74  55]
  [ 28  76  58]
  ...
  [ 33  47  36]
  [ 37  51  40]
  [ 39  53  42]]

 [[ 25  71  52]
  [ 27  73  54]
  [ 26  75  55]
  ...
  [ 34  47  39]
  [ 38  52  41]
  [ 40  53  45]]

 [[ 27  74  52]
  [ 27  74  52]
  [ 24  73  51]
  ...
  [ 36  48  42]
  [ 39  52  44]
  [ 41  53  47]]

 ...

 [[ 32  99  48]
  [ 34 101  50]
  [ 33 102  51]
  ..

  0%|          | 11/6149 [00:00<04:38, 22.01it/s]

...

[[[  2  28  10]
  [  0  28   9]
  [  0  26   7]
  ...
  [ 56  88  69]
  [ 56  88  69]
  [ 53  88  68]]

 [[  4  30  12]
  [  3  31  12]
  [  4  32  13]
  ...
  [ 70 100  81]
  [ 67  99  80]
  [ 66  98  79]]

 [[  1  27   9]
  [  2  30  11]
  [  8  36  17]
  ...
  [ 83 110  94]
  [ 81 110  94]
  [ 80 109  93]]

 ...

 [[  1  27  11]
  [  3  30  14]
  [  4  33  18]
  ...
  [ 16  40  64]
  [ 16  40  64]
  [ 16  38  66]]

 [[  3  29  13]
  [  6  33  17]
  [  9  38  23]
  ...
  [ 19  43  67]
  [ 19  43  67]
  [ 19  41  69]]

 [[  4  30  14]
  [  7  34  18]
  [ 11  40  25]
  ...
  [ 19  43  67]
  [ 19  43  67]
  [ 19  41  69]]]
[[[16 34 27]
  [14 32 25]
  [13 29 22]
  ...
  [ 0 11  7]
  [ 0 11  7]
  [ 0 10  8]]

 [[12 30 23]
  [10 28 21]
  [10 26 19]
  ...
  [ 0 13  9]
  [ 0 13  9]
  [ 0 12 10]]

 [[ 8 24 17]
  [ 7 23 16]
  [ 8 24 17]
  ...
  [ 1 15  9]
  [ 1 15  9]
  [ 3 14 11]]

 ...

 [[ 4 24 12]
  [ 6 26 14]
  [ 9 29 17]
  ...
  [17 42 22]
  [18 43 23]
  [18 42 24]]

 [[ 9 29 17]
  [11 3

100%|█████████▉| 6130/6149 [01:20<00:00, 84.47it/s]

[[[ 81  32 116]
  [ 82  33 117]
  [ 82  33 117]
  ...
  [ 28  34  29]
  [ 28  34  29]
  [ 28  34  29]]

 [[ 81  32 116]
  [ 81  32 116]
  [ 82  33 117]
  ...
  [ 27  33  28]
  [ 27  33  28]
  [ 27  33  28]]

 [[ 80  32 114]
  [ 81  33 115]
  [ 82  34 116]
  ...
  [ 27  33  28]
  [ 27  33  28]
  [ 27  33  28]]

 ...

 [[ 31  55  45]
  [ 31  55  45]
  [ 31  55  45]
  ...
  [ 27  33  28]
  [ 27  33  28]
  [ 27  33  28]]

 [[ 30  54  44]
  [ 30  54  44]
  [ 30  54  44]
  ...
  [ 27  33  28]
  [ 27  33  28]
  [ 27  33  28]]

 [[ 29  53  43]
  [ 29  53  43]
  [ 29  53  43]
  ...
  [ 27  33  28]
  [ 27  33  28]
  [ 27  33  28]]]
[[[12 52 27]
  [10 50 25]
  [ 6 48 23]
  ...
  [20 47 31]
  [17 51 27]
  [15 52 26]]

 [[18 58 33]
  [13 55 30]
  [ 9 51 26]
  ...
  [16 43 27]
  [16 50 26]
  [14 51 25]]

 [[20 63 36]
  [16 59 32]
  [11 54 27]
  ...
  [11 38 22]
  [16 47 26]
  [14 48 24]]

 ...

 [[24 40 63]
  [24 40 63]
  [26 40 63]
  ...
  [ 4 40 18]
  [ 3 50 24]
  [19 70 42]]

 [[20 36 59]
  [20 3

100%|██████████| 6149/6149 [01:20<00:00, 76.63it/s]

[[[ 8 24 23]
  [ 8 22 21]
  [ 6 19 17]
  ...
  [15 24 21]
  [15 24 21]
  [14 23 20]]

 [[ 7 23 22]
  [ 7 21 20]
  [ 7 20 18]
  ...
  [14 23 20]
  [14 23 20]
  [14 23 20]]

 [[ 7 21 20]
  [ 7 21 20]
  [ 7 20 18]
  ...
  [13 22 19]
  [13 22 19]
  [13 22 19]]

 ...

 [[ 4  9  8]
  [ 4  9  8]
  [ 3  8  7]
  ...
  [ 5  7  7]
  [ 5  7  7]
  [ 5  7  7]]

 [[ 6 11 10]
  [ 5 10  9]
  [ 5 10  9]
  ...
  [ 5  7  7]
  [ 5  7  7]
  [ 5  7  7]]

 [[ 7 12 11]
  [ 6 11 10]
  [ 6 11 10]
  ...
  [ 6  8  8]
  [ 6  8  8]
  [ 6  8  8]]]
[[[125 142 145]
  [124 141 144]
  [124 141 144]
  ...
  [108 122 134]
  [108 122 134]
  [108 122 134]]

 [[125 142 145]
  [124 141 144]
  [124 141 144]
  ...
  [108 122 134]
  [108 122 134]
  [108 122 134]]

 [[125 142 145]
  [124 141 144]
  [124 141 144]
  ...
  [108 122 134]
  [108 122 134]
  [108 122 134]]

 ...

 [[ 90  67 119]
  [ 90  67 119]
  [ 90  67 119]
  ...
  [ 76  64  94]
  [136 123 155]
  [137 122 154]]

 [[ 90  67 119]
  [ 90  67 119]
  [ 90  67 119]
  ...
  

In [ ]:
y_pred = model.predict(X_test)
y_pred = np.argmax(y_pred, axis = 1)



test_files = [('test/'+x) for (x) in os.listdir(test_location)]

print(test_files[0])

sorted_preds = []
for i in range (0, len(X_test)):
    pred =  ((test_files[i]), y_pred[i])
    sorted_preds.append(pred)
 
sorted_preds = sorted(sorted_preds, key=lambda prediction: prediction[0])
with open("submission_sample.csv".format(test_location), "w+", newline = "") as f:
    writer = csv.writer(f)
    writer.writerow(['file_path','label'])
    for i in range (0, len(X_test)):
        writer.writerow([(sorted_preds[i][0]), (sorted_preds[i][1])])

print("Submission_sample.csv updated successfully")



In [ ]:
files.download("submission_sample.csv")